## DeepDream with VGG16

<img src="http://science.slc.edu/jmarshall/bioai/images/dd1_small.jpg" width="55%">

The DeepDream algorithm is almost identical to the filter-visualization technique we explored for individual filters, in which we used gradient ascent to find an input image that maximizes the response of a particular filter within a layer.  But there are three key differences:

* DeepDream finds an image that maximizes the activation of an entire set of layers rather than a specific filter within a layer.
* Instead of starting with a noisy blank image, we start with an existing image.
* Input images are processed at different scales, called *octaves*.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import tensorflow
tensorflow.compat.v1.disable_eager_execution()  # workaround for TF2

We'll load just the pretrained VGG16 convolutional base, without the classification layers, so that we can feed images of any size into the network.

In [ ]:
from tensorflow.keras.applications import VGG16

vgg16 = VGG16(weights='imagenet', include_top=False)

In [ ]:
vgg16.summary()

### Utility Functions for Processing Images

In [ ]:
import tensorflow as tf

def load_image_from_file(filename):
    url = "http://science.slc.edu/jmarshall/bioai/images/" + filename
    image_path = tf.keras.utils.get_file(filename, origin=url)
    jpeg_img = tf.keras.utils.load_img(image_path)
    return np.array(jpeg_img)

In [ ]:
elephants = load_image_from_file('elephants.jpg')
baby = load_image_from_file('baby_elephant.jpg')
jellyfish = load_image_from_file('jellyfish.jpg')
flamingos = load_image_from_file('flamingos.jpg')
tiger = load_image_from_file('tiger.jpg')

In [ ]:
from tensorflow.keras.applications.inception_v3 import preprocess_input

# converts an image of ints in the range [0, 255] to a batch tensor
# of shape (1, height, width, 3) of floats in the range [-1.0, 1.0]

def pre_process(image):
    return np.array([preprocess_input(image)])

In [ ]:
# converts a batch tensor of floats into a displayable image of ints in the range [0, 255]

def post_process(x):
    x = x.reshape((x.shape[1], x.shape[2], 3))  # reshapes x as a single image
    x = (x / 2 + 0.5) * 255  # rescales the range [-1.0, 1.0] to [0.0, 255.0]
    x = x.clip(0, 255).astype('uint8')  # converts all values to ints in the range [0, 255]
    return x

In [ ]:
import scipy

# img: a batch tensor of shape (1, height, width, 3)
# new_size: a tuple (new_height, new_width)

def resize(img, new_size):
    img = img.copy()
    factors = (1, new_size[0]/img.shape[1], new_size[1]/img.shape[2], 1)
    return scipy.ndimage.zoom(img, factors, order=1)

### Gradient Ascent in Input-Image Space

In [ ]:
import tensorflow.keras.backend as K

Since we are using a pretrained network with no learning involved, we disable all training-specific operations:

In [ ]:
K.set_learning_phase(0)

This dictionary specifies which layers of the VGG16 network will be used to construct the dream image, as well as their relative weightings:

In [ ]:
layer_contributions = {
    'block1_conv1': 1.0,
    'block2_conv1': 1.0,
    'block3_conv1': 2.0,
    'block4_conv1': 3.0,
    'block5_conv1': 1.0,
}

This builds the function to be optimized:

In [ ]:
def build_value_function(model):
    value = K.variable(0.0)

    # add up the contributions from each layer
    for layer_name, coeff in layer_contributions.items():
        activation = model.get_layer(layer_name).output
        value = value + coeff * K.mean(K.square(activation))
        
    # grad is the derivative of value with respect to the model's input tensor
    grad = K.gradients(value, model.input)[0]
    
    # normalize the gradient (safely)
    grad /= K.maximum(1e-7, K.mean(K.abs(grad)))
    
    # create the function to be iterated
    f = K.function([model.input], [value, grad])
    return f

This performs gradient ascent on a function f starting from an input x:

In [ ]:
def gradient_ascent(x, f, cycles, step_size, quiet=True):
    for i in range(1, cycles+1):
        value, gradient = f([x])
        if not quiet:
            print("...value on cycle {}: {}".format(i, value))
        x += gradient * step_size
    return x

### The DeepDream Algorithm

<img src="http://science.slc.edu/jmarshall/bioai/images/dd_algorithm.jpg" width="90%">

In [ ]:
def size_sequence(height, width, num_octaves=3, scale_factor=1.4):
    sizes = [(height, width)]
    for i in range(1, num_octaves):
        height, width = int(height/scale_factor), int(width/scale_factor)
        sizes.append((height, width))
    return sizes[::-1]  # reverses the list

### Parameters
<pre>
cycles          <i>maximum number of cycles of gradient ascent</i>
step_size       <i>gradient ascent step size</i>
num_octaves     <i>number of dream/upscale cycles</i>
scale_factor    <i>upscale factor</i>
quiet           <i>controls level of output</i>
</pre>

In [ ]:
def deep_dream(image, cycles=20, step_size=0.01, num_octaves=3, scale_factor=1.4, quiet=False):
    # image can be a numpy image or a filename string
    if type(image) == np.ndarray and image.dtype == 'uint8':
        pass
    elif type(image) == str:
        image = load_image_from_file(image)
    else:
        print("image must be an int array in the range [0,255] or an image filename")
        return
    
    f = build_value_function(vgg16)
    
    height, width = image.shape[0], image.shape[1]
    sizes = size_sequence(height, width, num_octaves, scale_factor)

    # converts image to a batch tensor of float32 values in the range [-1.0, 1.0]
    original = pre_process(image)
    scaled_originals = [resize(original, size) for size in sizes]
    
    img = scaled_originals[0].copy()
    for i in range(num_octaves):
        if not quiet:
            print("Processing image size", sizes[i])
        # dream
        img = gradient_ascent(img, f, cycles, step_size, quiet)
        if i != num_octaves-1:
            # upscale image
            img = resize(img, sizes[i+1])
            # reinject lost details
            upscaled_original = resize(scaled_originals[i], sizes[i+1])
            lost_detail = scaled_originals[i+1] - upscaled_original
            img += lost_detail
  
    dream = post_process(img)

    plt.imshow(dream)
    plt.axis('off')
    plt.show()
    
    #scipy.misc.imsave('dream.png', dream)
    #print('Image saved as dream.png')

In [ ]:
plt.imshow(jellyfish);

In [ ]:
plt.imshow(tiger);

In [ ]:
plt.imshow(flamingos);

In [ ]:
layer_contributions = {
    'block1_conv1': 1.0,
    'block2_conv1': 2.0,
}
deep_dream(elephants, cycles=15)

### A VGG16 DeepDream Gallery

In [ ]:
layer_contributions = {
    'block2_conv1': 1.0,
    'block3_conv1': 2.0,
}
deep_dream(elephants, cycles=15, quiet=True)

In [ ]:
layer_contributions = {
    'block1_conv1': 1.0,
    'block2_conv1': 1.0,
    'block3_conv1': 2.0,
    'block4_conv1': 3.0,
    'block5_conv1': 1.0,
}
deep_dream(elephants, cycles=15, quiet=True)

In [ ]:
layer_contributions = {
    'block2_conv1': 1.0,
    'block3_conv1': 5.0,
}
deep_dream(tiger, cycles=15, quiet=True)

In [ ]:
layer_contributions = {
    'block1_conv1': 1.0,
}
deep_dream(flamingos, cycles=20, num_octaves=3, scale_factor=1.4, quiet=True)

In [ ]:
layer_contributions = {
    'block2_conv1': 1.0,
}
deep_dream(flamingos, cycles=20, num_octaves=3, scale_factor=1.4, quiet=True)

In [ ]:
layer_contributions = {
    'block3_conv1': 1.0,
}
deep_dream(flamingos, cycles=20, num_octaves=3, scale_factor=1.4, quiet=True)

In [ ]:
layer_contributions = {
    'block3_conv1': 1.0,
    'block4_conv1': 5.0,
}
deep_dream(flamingos, cycles=20, num_octaves=3, scale_factor=1.4, quiet=True)

In [ ]:
layer_contributions = {
    'block1_conv1': 1.0,
    'block3_conv1': 2.0,
    'block4_conv1': 3.0,
}
deep_dream(flamingos, cycles=20, num_octaves=6, scale_factor=1.9, quiet=True)

In [ ]:
layer_contributions = {
    'block3_conv2': 1.0,
}
deep_dream(jellyfish, cycles=20, num_octaves=3, scale_factor=1.4, quiet=True)

In [ ]:
layer_contributions = {
    'block4_conv1': 1.0,
}
deep_dream(jellyfish, cycles=20, num_octaves=3, scale_factor=1.4, quiet=True)

In [ ]:
layer_contributions = {
    'block4_pool': 1.0,
}
deep_dream(jellyfish, cycles=20, num_octaves=3, scale_factor=1.4, quiet=True)

In [ ]:
layer_contributions = {
    'block4_conv2': 3.0,
    'block5_conv1': 1.0,
}
deep_dream(jellyfish, cycles=20, num_octaves=3, scale_factor=1.4, quiet=True)

In [ ]:
layer_contributions = {
    'block1_conv1': 3.0,
    'block4_conv1': 1.0,
}
deep_dream(tiger, cycles=20, num_octaves=3, scale_factor=1.4, quiet=True)

In [ ]:
layer_contributions = {
    'block1_conv1': 3.0,
    'block2_conv1': 2.0,
    'block3_conv1': 1.0,
}
deep_dream(tiger, cycles=20, num_octaves=4, scale_factor=1.9, quiet=True)

In [ ]:
layer_contributions = {
    'block5_conv1': 1.0,
}
deep_dream(tiger, cycles=20, num_octaves=8, scale_factor=1.3, quiet=True)

In [ ]:
layer_contributions = {
    'block5_conv1': 1.0,
}
deep_dream(tiger, cycles=20, num_octaves=7, scale_factor=1.7, quiet=True)

In [ ]:
layer_contributions = {
    'block5_conv1': 1.0,
}
deep_dream(tiger, cycles=20, num_octaves=6, scale_factor=1.67, quiet=True)

In [ ]:
layer_contributions = {
    'block5_conv1': 1.0,
}
deep_dream(tiger, cycles=20, num_octaves=6, scale_factor=1.64, quiet=True)

In [ ]:
layer_contributions = {
    'block1_conv1': 1.0,
    'block2_conv1': 1.0,
    'block5_conv1': 5.0,
}
deep_dream(elephants, cycles=20, num_octaves=4, scale_factor=1.6, quiet=True)

In [ ]:
layer_contributions = {
    'block1_conv1': 1.0,
    'block2_conv1': 1.0,
    'block5_conv1': 5.0,
}
deep_dream(elephants, cycles=20, num_octaves=8, scale_factor=1.6, quiet=True)

In [ ]:
layer_contributions = {
    'block1_conv1': 1.0,
    'block2_conv1': 1.0,
    'block5_conv2': 5.0,
}
deep_dream(elephants, cycles=30, num_octaves=8, scale_factor=1.6, quiet=True)

In [ ]:
layer_contributions = {
    'block1_conv1': 1.0,
    'block2_conv1': 1.0,
    'block5_conv2': 5.0,
}
deep_dream(elephants, cycles=20, num_octaves=8, scale_factor=1.7, quiet=True)